In [5]:
import json
import networkx as nx
#import wget
#import igraph as ig
import tweepy
import numpy as np
import matplotlib.pyplot as plt

# for homeless tweets

In [ ]:
# Save the location of the Tweet JSON file
f1 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homeless_tweets_0329.json")
TWEET_JSON1 = json.load(f1)
f2 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homeless_tweets_0407.json")
TWEET_JSON2 = json.load(f2)
f3 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homeless_tweets_0414.json")
TWEET_JSON3 = json.load(f3)
f4 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homeless0221.json")
TWEET_JSON4 = json.load(f4)
f5 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homeless0310.json")
TWEET_JSON5 = json.load(f5)
f6 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homeless0321.json")
TWEET_JSON6 = json.load(f6)

#merge multiple JSON file
all_data = TWEET_JSON1 + TWEET_JSON2 + TWEET_JSON3 + TWEET_JSON4 + TWEET_JSON5 + TWEET_JSON6

In [7]:
info = {"api_key": "EA0Nc1ZdovL6026feB6QzC42a",
        "api_key_secret": "bbnyEELzI06L3pNCfHdLeOkTio5L6kT5KKH4eKRUXwfNrG4JQ",
        "bearer_token" : "AAAAAAAAAAAAAAAAAAAAAA2hYgEAAAAA8OUr3Ab8wV2SBd7AQz3UxblZ%2FFM%3Dl5bbd1hC9D6tsWDN1HNtqm1SHC4Dgy56ZrjwPr4FlJWWFE8E3K",
        "access_token": "1487509017362513921-lZvWsFfvOFrSyO1pRwMJ1nIxpuA2oi",
        "access_token_secret": "wm7cetupMABoics4sHxrzKeC9TpDEB4mGVRMEEkqDZr72"}

client = tweepy.Client(
    consumer_key       = info["api_key"],
    consumer_secret    = info["api_key_secret"],
    bearer_token       = info["bearer_token"],
    access_token       = info["access_token"],
    access_token_secret= info["access_token_secret"],
    wait_on_rate_limit = True
)

fields = "id,public_metrics"


fields = "created_at,lang,author_id,text,referenced_tweets" 
expansions = "attachments.media_keys,referenced_tweets.id,author_id"

In [11]:
#try out mine own codes
def clean_tweet(tweet): 
    processed_tweet = {
        "id" : tweet['id'], 
        #"user" : tweet['author_id'], 
        "created_at" : tweet['created_at'], 
        "text" : ""
    }
    if "extended_tweet" in tweet: 
        processed_tweet["text"] = tweet['extended_tweet']['full_text']
    elif "full_text" in tweet: 
        processed_tweet["text"] = tweet['full_text']
    elif "text" in tweet: 
        processed_tweet["text"] = tweet['text']
        
    if 'referenced_tweets' in tweet:
        rt = tweet['referenced_tweets']
        processed_tweet["is_rt"] = True
        processed_tweet["rt_id"] = rt[0]['id'] 
        processed_tweet["rt_text"] = ""
        if 'extended_tweet' in rt: 
            processed_tweet["rt_text"] = rt['extended_tweet']['full_text']
        elif "full_text" in rt:
            processed_tweet["rt_text"] = rt['full_text']
        elif "text" in rt: 
            processed_tweet["rt_text"] = rt['text']
    else: 
        processed_tweet["is_rt"] = False
            
    return processed_tweet

tweet_data = []       
for line in all_data:
    tweet_data.append(line)

# filter all of the raw tweets by turning them into clean_tweet objects
# the filtering is taken care of in the class function
filtered_data = []
for elem in tweet_data: 
    filtered_tweet = clean_tweet(elem)
    filtered_data.append(filtered_tweet)

In [12]:
# printing the first element of the unfiltered data as an example
print(tweet_data[0])
print ("---")
# printing an example of a retweet object as an example
print(tweet_data[1])

{'referenced_tweets': [{'type': 'retweeted', 'id': '1508732023233708037'}], 'lang': 'en', 'created_at': '2022-03-29T21:53:59.000Z', 'author_id': '1364018677503332354', 'text': 'RT @hepcatsector: yup, ask the guy who bit off a homeless guys ear for calling him Jonathan Creek what he thinks about handling jokes.', 'id': '1508925463942483968', 'is_rt': True, 'rt_id': '1508732023233708037', 'rt_text': 'yup, ask the guy who bit off a homeless guys ear for calling him Jonathan Creek what he thinks about handling jokes. https://t.co/2onwVzzqVd'}
---
{'referenced_tweets': [{'type': 'retweeted', 'id': '1508733312310915075'}], 'lang': 'en', 'created_at': '2022-03-29T21:53:59.000Z', 'author_id': '1163910383507128320', 'text': 'RT @rachel_cheung1: In Dec 2019, a group of 14 homeless people were evicted by authorities from a park in Sham Shui Po. Their personal belo…', 'id': '1508925463846002689', 'is_rt': True, 'rt_id': '1508733312310915075', 'rt_text': 'In Dec 2019, a group of 14 homeless people 

In [13]:
# how many total tweets we have
len(filtered_data)

41048

# Getting retweets

In [28]:
# construct a directed graph for retweet graph
G=nx.DiGraph()

for elem in filtered_data: 
    # for each tweet, we add the tweet's user to the graph
    G.add_node(elem["id"])
    print (elem["id"])

    # if this tweet is a retweet, we add the original tweet's user to the graph
    # and create an edge between the current user and the original tweet's user
    # current user -> original tweet's user
    if elem["is_rt"]: 
        G.add_node(elem["rt_id"], name = 'elem["rt_id"]')
        print (elem["rt_id"])
        G.add_edge(elem["id"], elem["rt_id"])
    print ("--")

1508925463942483968
1508732023233708037
--
1508925463846002689
1508733312310915075
--
1508925460427816962
1508545054075498500
--
1508925456292192256
1508293131409625090
--
1508925454308282368
1508902279574917133
--
1508925453943263232
--
1508925449916801030
1508622976673005568
--
1508925443369418753
1508540952864079894
--
1508925438332182538
1508922312573153282
--
1508925432258781184
1508922951734755329
--
1508925431717584897
1508783469643673612
--
1508925430836785154
--
1508925430463614976
1507451084616392709
--
1508925415158648837
1508512761327853575
--
1508925399686066176
1508909537482268673
--
1508925397542473728
--
1508925380626894859
1508887032965214211
--
1508925368266330118
1508919628730413059
--
1508925367691661317
--
1508925364134887428
1508912105122156548
--
1508925361475751945
1508901626689560577
--
1508925359458238470
1508887032965214211
--
1508925353254965259
1508924843244277768
--
1508925351287795719
1508868471932825614
--
1508925349215846404
1508515914714656769
--
15089

1508920622952423424
1454050557858045954
--
1508920606988853250
1508823093837504521
--
1508920606112337921
1508906107577716753
--
1508920599350972416
1508912816656367633
--
1508920591230943242
1508892394590466048
--
1508920587036545033
1508572389747019781
--
1508920583093985287
1508540952864079894
--
1508920577075159044
--
1508920562168573958
1508906107577716753
--
1508920554882932736
1508646694782652420
--
1508920553796775944
1508544491585687557
--
1508920552584450048
1508712036846694403
--
1508920552093798404
1508810112697356292
--
1508920543172464640
--
1508920542748979205
--
1508920535903842304
1508887032965214211
--
1508920532003176451
1508822650369589264
--
1508920523513860110
1508920137369497607
--
1508920507789312001
1508893268569825281
--
1508920506363359242
1508895079481716741
--
1508920503796346881
1508919051912949764
--
1508920501074280456
--
1508920496729042945
1508905260106108932
--
1508920494539517954
1508916879036850176
--
1508920492371050497
1508887032965214211
--
15089

1508916006416265224
1508912260990836744
--
1508915997864083458
1508794582603022337
--
1508915995922300930
--
1508915990104621059
1508293131409625090
--
1508915988481421332
1508906107577716753
--
1508915980818395137
--
1508915970856861697
1508915826317004807
--
1508915969795702786
1508897641459036165
--
1508915955614715906
1508555383597682688
--
1508915948966883339
1508906107577716753
--
1508915929706643459
1508540952864079894
--
1508915927936602117
--
1508915925327646722
--
1508915915324375048
1508540952864079894
--
1508915910244896771
1506843117265514496
--
1508915898148659200
1508887032965214211
--
1508915895770521601
1505015860318154753
--
1508915889084645376
1508856537921507335
--
1508915887360815109
--
1508915886572380174
1508909297580748802
--
1508915886052237314
1508844712614146057
--
1508915878821199874
1508895079481716741
--
1508915864816570372
1508906107577716753
--
1508915843966590990
1508544491585687557
--
1508915833917034509
1508836461596008454
--
1508915832189034502
15086

1508912777611517953
1508906107577716753
--
1508912775153782791
--
1508912773241131009
1508540952864079894
--
1508912766710693892
1508540952864079894
--
1508912764659638274
1508895079481716741
--
1508912759605497856
1508848806854639620
--
1508912744967421957
--
1508912743608430598
1508716890801074176
--
1508912739078619146
--
1508912737241415680
1508526372674625536
--
1508912731021357062
1508622976673005568
--
1508912728622174232
1508816815123836938
--
1508912714671865867
--
1508912711895244801
1508622976673005568
--
1508912703456391177
1508318239083872258
--
1508912700079759361
--
1508912693738049539
1508908558326325250
--
1508912682916843521
1508895079481716741
--
1508912671990636549
1508911609330253826
--
1508912671550287872
1508903524897366026
--
1508912670728241159
1508518044611526659
--
1508912668203180033
1508906107577716753
--
1508912661777592330
1508887032965214211
--
1508912651593990144
1508892394590466048
--
1508912647965618176
1508832924099133440
--
1508912645495263232
15085

1508515914714656769
--
1508908797330595840
1508556281493147649
--
1508908795786895367
1508540952864079894
--
1508908792817274880
1508545054075498500
--
1508908792221687808
1508640096811159554
--
1508908791840059399
1508485326372757512
--
1508908779626131458
--
1508908768620392450
--
1508908748760395784
1508868471932825614
--
1508908741428662276
1508832378378022918
--
1508908740430671873
1508545054075498500
--
1508908719899385865
1508770264082960389
--
1508908719651758090
1508890501210161159
--
1508908716799799303
1508622976673005568
--
1508908713775575041
1508622976673005568
--
1508908704418123783
1508545054075498500
--
1508908703944085504
1508545054075498500
--
1508908692653191168
1508820038521815041
--
1508908683777949718
1508540952864079894
--
1508908680808644608
1508820038521815041
--
1508908679176679424
1508540952864079894
--
1508908675309654016
1508908486972825607
--
1508908661707616270
1508292884419604487
--
1508908648067739659
1508908299705622538
--
1508908644653363200
15086229

...

1506050097980878849
--
1506050091810971648
--
1506050085058068484
--
1506050081937534977
--
1506050077751595009
--
1506050077663678469
--
1506050073397895168
--
1506050062438305794
--
1506050062295654404
--
1506050061934870533
--
1506050053017845766
--
1506050033619197957
--
1506050029764685824
--
1506050028267532289
--
1506049982163558402
--
1506049978099187720
--
1506049962102214659
--
1506049961972150273
--
1506049955425038339
--
1506049950953705481
--
1506049932981153794
--
1506049932540592129
--
1506049917571239937
--
1506049915121664002
--
1506049913917952005
--
1506049912751865856
--
1506049908545105923
--
1506049898344595470
--
1506049893525250049
--
1506049892707442700
--
1506049872914395136
--
1506049866430042122
--
1506049866283290628
--
1506049855021629443
--
1506049846180200451
--
1506049845924085767
--
1506049838072406016
--
1506049834410778627
--
1506049830073864193
--
1506049817260158977
--
1506049797156917250
--
1506049791599562753
--
1506049786830471172
--
15060497829

1506037235577024514
--
1506037228765687812
--
1506037228602073094
--
1506037228283310094
--
1506037220012089351
--
1506037178270461958
--
1506037161212186627
--
1506037141025042446
--
1506037127125028873
--
1506037124235157513
--
1506037123798867970
--
1506037122389659656
--
1506037120879583233
--
1506037114592444418
--
1506037090399793154
--
1506037087329521671
--
1506037041338875908
--
1506037038617075715
--
1506037035504746508
--
1506037018752606219
--
1506037015179104261
--
1506037012310204421
--
1506037002973728779
--
1506036984007045121
--
1506036979326087170
--
1506036973231919105
--
1506036937379000328
--
1506036921876684805
--
1506036918735323146
--
1506036910199869445
--
1506036909436391426
--
1506036907968544773
--
1506036901450555395
--
1506036889089761280
--
1506036882592997378
--
1506036879287885831
--
1506036875181522948
--
1506036872111222786
--
1506036863811088384
--
1506036863609581570
--
1506036834186448911
--
1506036831023996932
--
1506036822685765642
--
15060368029

--
1506024395126439937
--
1506024384573583360
--
1506024376973799425
--
1506024367620341763
--
1506024366600908802
--
1506024362742202368
--
1506024361857327105
--
1506024350671151117
--
1506024342664192018
--
1506024327459782660
--
1506024318811054081
--
1506024317301059584
--
1506024304638664709
--
1506024287928528897
--
1506024283629309958
--
1506024272979972097
--
1506024269691588612
--
1506024263316381705
--
1506024261277962240
--
1506024254097272833
--
1506024243733037057
--
1506024240574775304
--
1506024238410575880
--
1506024235449393154
--
1506024215044136962
--
1506024214045863937
--
1506024213336969224
--
1506024213051633664
--
1506024210552193025
--
1506024210384056324
--
1506024207209140231
--
1506024204960878592
--
1506024196744355841
--
1506024190729543683
--
1506024190255710211
--
1506024183532175362
--
1506024181388828674
--
1506024180193529859
--
1506024177949716487
--
1506024174069825536
--
1506024171263954950
--
1506024170055999492
--
1506024165148696578
--
15060241

1506011726004862977
--
1506011724146941952
--
1506011722112385029
--
1506011703141576709
--
1506011702331994118
--
1506011700512059395
--
1506011675493015561
--
1506011670958985216
--
1506011668760784896
--
1506011630907588610
--
1506011612041293832
--
1506011612028628994
--
1506011609860546563
--
1506011607465398275
--
1506011607167504385
--
1506011606425423873
--
1506011604571549699
--
1506011601413246977
--
1506011599630659586
--
1506011579728674816
--
1506011564511404048
--
1506011563924332544
--
1506011559440490496
--
1506011558228676610
--
1506011551790075914
--
1506011544584343557
--
1506011542914953217
--
1506011538171351040
--
1506011529124098051
--
1506011528423739393
--
1506011508811128832
--
1506011482969952256
--
1506011479849734152
--
1506011452208910340
--
1506011444206206979
--
1506011425957122048
--
1506011413533245445
--
1506011408336834565
--
1506011396357902337
--
1506011395066056709
--
1506011366125371394
--
1506011360605655040
--
1506011356981456896
--
15060113559

1505997927658913793
--
1505997913796792324
--
1505997906293235713
--
1505997899523670021
--
1505997897262845956
--
1505997871467753472
--
1505997867768434690
--
1505997861917540360
--
1505997860172615688
--
1505997858180374531
--
1505997854900428800
--
1505997853759528971
--
1505997836126674950
--
1505997825963929601
--
1505997822520446979
--
1505997808763035652
--
1505997805826891777
--
1505997793487474689
--
1505997791780380685
--
1505997788378648576
--
1505997763598761985
--
1505997736755216386
--
1505997732644745216
--
1505997724671516678
--
1505997722796630034
--
1505997722557558795
--
1505997688772333569
--
1505997680366944259
--
1505997668450983939
--
1505997666458943488
--
1505997662109151233
--
1505997660943224836
--
1505997652663717895
--
1505997649102741512
--
1505997648049942532
--
1505997643658366977
--
1505997624817721345
--
1505997622691209222
--
1505997620480675840
--
1505997620027826177
--
1505997586443997189
--
1505997585340936199
--
1505997583067492353
--
15059975830

In [21]:
# printing out the number of nodes (users) in our graph
print (len(G.nodes()))
# printing out the number of edges/links in our graph
print (len(G.edges()))

46993
27184


In [ ]:
# writing our graph to a Gephi file format
nx.write_gexf(G, "homeless_retweets.gexf")

# Getting and Analysing the huge nodes

In [32]:
#get the huge nodes

sorted(G.degree, key=lambda x: x[1], reverse=True)


#########################################
#############     TOP5     ##############
#########################################
#('1511511675660341249', 2779),
#('1508545054075498500', 1308),
#('1514632306635382789', 747),
#('1514358189692637188', 652),
#('1508887032965214211', 641)

[('1511511675660341249', 2779),
 ('1508545054075498500', 1308),
 ('1514632306635382789', 747),
 ('1514358189692637188', 652),
 ('1508887032965214211', 641),
 ('1508540952864079894', 451),
 ('1514442354811416581', 443),
 ('1508622976673005568', 434),
 ('1514322469338767364', 417),
 ('1508890501210161159', 282),
 ('1508823093837504521', 278),
 ('1508544491585687557', 276),
 ('1511842275164397573', 272),
 ('1514618389775323142', 250),
 ('1514632257843122178', 241),
 ('1508515914714656769', 235),
 ('1508895079481716741', 216),
 ('1514313292122140683', 209),
 ('1514637113450450945', 197),
 ('1514621059718426626', 182),
 ('1508574893121622022', 178),
 ('1511904409449648137', 176),
 ('1514321584873422854', 176),
 ('1514598661728129027', 152),
 ('1514373243888717824', 142),
 ('1511721054263132160', 139),
 ('1508293131409625090', 117),
 ('1514606088095625216', 115),
 ('1508820363446296584', 113),
 ('1511717601612763141', 110),
 ('1514639329716576258', 110),
 ('1508892394590466048', 108),
 ('150

In [35]:
info = {"api_key": "EA0Nc1ZdovL6026feB6QzC42a",
        "api_key_secret": "bbnyEELzI06L3pNCfHdLeOkTio5L6kT5KKH4eKRUXwfNrG4JQ",
        "bearer_token" : "AAAAAAAAAAAAAAAAAAAAAA2hYgEAAAAA8OUr3Ab8wV2SBd7AQz3UxblZ%2FFM%3Dl5bbd1hC9D6tsWDN1HNtqm1SHC4Dgy56ZrjwPr4FlJWWFE8E3K",
        "access_token": "1487509017362513921-lZvWsFfvOFrSyO1pRwMJ1nIxpuA2oi",
        "access_token_secret": "wm7cetupMABoics4sHxrzKeC9TpDEB4mGVRMEEkqDZr72"}

client = tweepy.Client(
    consumer_key       = info["api_key"],
    consumer_secret    = info["api_key_secret"],
    bearer_token       = info["bearer_token"],
    access_token       = info["access_token"],
    access_token_secret= info["access_token_secret"],
    wait_on_rate_limit = True
)

In [39]:
#Analysing the TOP5 tweets
TOP1_tweet = client.get_tweet(1511511675660341249)
print(TOP1_tweet)
#https://twitter.com/Native4life3/status/1511511675660341249

TOP2_tweet = client.get_tweet(1508545054075498500)
print(TOP2_tweet)
#https://twitter.com/shaeloe/status/1508545054075498500

TOP3_tweet = client.get_tweet(1514632306635382789)
print(TOP3_tweet)
#https://twitter.com/TheRickyDavila/status/1514632306635382789

TOP4_tweet = client.get_tweet(1514358189692637188)
print(TOP4_tweet)
#https://twitter.com/LammaticHama/status/1514358189692637188

TOP5_tweet = client.get_tweet(1508887032965214211)
print(TOP5_tweet)
#https://twitter.com/RBReich/status/1508887032965214211

Response(data=<Tweet id=1511511675660341249 text='Homeless man saved 4 girls in that horrible shooting in Sacramento.  He huddled them in the doorway where he slept  blocking them with his body, so they would not be shot. The family is trying to find him so they can give him a helping hand up and off the street. His name is Tim.'>, includes={}, errors=[], meta={})
Response(data=<Tweet id=1508545054075498500 text='the equivalent to girls who are immediately loved by small animals and babies are guys who are immediately trusted by schizophrenics and the homeless'>, includes={}, errors=[], meta={})
Response(data=<Tweet id=1514632306635382789 text='A corrupt unstable billionaire would offer to pay $43B to buy Twitter, but not help feed the hungry, house the homeless, fund education or help our veterans? That sounds about right.'>, includes={}, errors=[], meta={})
Response(data=<Tweet id=1514358189692637188 text='"That homeless guys just gonna use that money for drugs!"\n\nMy brother in Chr

# for homelessness tweets

In [40]:
# Save the location of the Tweet JSON file
f7 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homelessness_tweets_0329.json")
TWEET_JSON7 = json.load(f7)
f8 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homelessness_tweets_0407.json")
TWEET_JSON8 = json.load(f8)
f9 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homelessness_tweets_0414.json")
TWEET_JSON9 = json.load(f9)
f10 = open("/Users/planetyunnn/Desktop/HUSTLE/2022 Spring/COMM 557/Codes/Usable Data/homelessness0321.json")
TWEET_JSON10 = json.load(f10)

#merge multiple JSON file
all_data2 = TWEET_JSON7 + TWEET_JSON8 + TWEET_JSON9 + TWEET_JSON10

In [44]:
#try out mine own codes
def clean_tweet(tweet): 
    processed_tweet = {
        "id" : tweet['id'], 
        #"user" : tweet['author_id'], 
        "created_at" : tweet['created_at'], 
        "text" : ""
    }
    if "extended_tweet" in tweet: 
        processed_tweet["text"] = tweet['extended_tweet']['full_text']
    elif "full_text" in tweet: 
        processed_tweet["text"] = tweet['full_text']
    elif "text" in tweet: 
        processed_tweet["text"] = tweet['text']
        
    if 'referenced_tweets' in tweet:
        rt = tweet['referenced_tweets']
        processed_tweet["is_rt"] = True
        processed_tweet["rt_id"] = rt[0]['id'] 
        processed_tweet["rt_text"] = ""
        if 'extended_tweet' in rt: 
            processed_tweet["rt_text"] = rt['extended_tweet']['full_text']
        elif "full_text" in rt:
            processed_tweet["rt_text"] = rt['full_text']
        elif "text" in rt: 
            processed_tweet["rt_text"] = rt['text']
    else: 
        processed_tweet["is_rt"] = False
            
    return processed_tweet

tweet_data2 = []       
for line in all_data2:
    tweet_data2.append(line)

# filter all of the raw tweets by turning them into clean_tweet objects
# the filtering is taken care of in the class function
filtered_data2 = []
for elem in tweet_data2: 
    filtered_tweet = clean_tweet(elem)
    filtered_data2.append(filtered_tweet)

In [45]:
# printing the first element of the unfiltered data as an example
print(tweet_data2[0])
print ("---")
# printing an example of a retweet object as an example
print(tweet_data2[1])

{'text': 'RT @adamjohnsonNYC: “This” being rich people and tourists having to see homeless people, not the actual existence of 1000s of homelessness…', 'created_at': '2022-03-29T21:56:33.000Z', 'id': '1508926106941984771', 'author_id': '4822931098', 'referenced_tweets': [{'type': 'retweeted', 'id': '1508890501210161159'}], 'lang': 'en', 'is_rt': True, 'rt_id': '1508890501210161159', 'rt_text': '“This” being rich people and tourists having to see homeless people, not the actual existence of 1000s of homelessness ppl—98% of whom will have no shelter to replace the one the NYPD destroyed and 99.9% of whom will not be moved into permanent housing. This “this” is totally ok https://t.co/8hyLYJrXBo'}
---
{'text': "RT @JoshuaPotash: Once again, I don't understand people who think homelessness is a problem for cops to solve, not a problem for a house to…", 'created_at': '2022-03-29T21:56:31.000Z', 'id': '1508926101782990848', 'author_id': '1416146323204714499', 'referenced_tweets': [{'type': '

In [47]:
# how many total tweets we have
len(filtered_data2)

39899

In [51]:
# construct a directed graph for retweet graph
G2=nx.DiGraph()

for elem in filtered_data2: 
    # for each tweet, we add the tweet's user to the graph
    G2.add_node(elem["id"])
    print (elem["id"])

    # if this tweet is a retweet, we add the original tweet's user to the graph
    # and create an edge between the current user and the original tweet's user
    # current user -> original tweet's user
    if elem["is_rt"]: 
        G2.add_node(elem["rt_id"], name = 'elem["rt_id"]')
        print (elem["rt_id"])
        G2.add_edge(elem["id"], elem["rt_id"])
    print ("--")

1508926106941984771
1508890501210161159
--
1508926101782990848
1508643632039043073
--
1508926074029236227
1508913135209484289
--
1508926037505175553
1508643632039043073
--
1508926010795855872
1508635228574674944
--
1508926001132470272
1508739410367377409
--
1508925999785816065
--
1508925996543709188
1508643632039043073
--
1508925979565121536
1508890501210161159
--
1508925956962103299
1508892034991538178
--
1508925941455667202
1508643632039043073
--
1508925909927178243
1508571459333074945
--
1508925904575156238
1508890501210161159
--
1508925895490347017
1504619986580557829
--
1508925828041777153
1507309058860146727
--
1508925827412602891
1508838044346064902
--
1508925824619229185
1508890501210161159
--
1508925802531983361
1508890501210161159
--
1508925793413611520
1508838044346064902
--
1508925776799883267
1508643632039043073
--
1508925768306335744
--
1508925758508453888
1508811930504413195
--
1508925751277498368
1508643632039043073
--
1508925742188400640
1508893268569825281
--
15089257

--
1508911261286809632
1508890501210161159
--
1508911259747426307
1508838044346064902
--
1508911256635387904
1508890501210161159
--
1508911252633894917
1508907658895499266
--
1508911236787978251
1508643632039043073
--
1508911143783477251
1508643632039043073
--
1508911121352179716
--
1508911050871087107
1508840744970121216
--
1508911049260810240
1508759723289448448
--
1508911014665981954
1508643632039043073
--
1508910999058976768
1508643632039043073
--
1508910976451547137
--
1508910933220810755
1508890501210161159
--
1508910925008588806
1508643632039043073
--
1508910857316712452
1508643632039043073
--
1508910848382672899
1508857919730814976
--
1508910843592806403
1508857887572983811
--
1508910842267541518
1508643632039043073
--
1508910832482078720
1508857921588895756
--
1508910826463375361
1508910230872207363
--
1508910822445268995
1508630967925178370
--
1508910809879040012
1508643632039043073
--
1508910780007124992
1508890501210161159
--
1508910777599762434
1508643632039043073
--
15089

1508643632039043073
--
1508895914693468178
1508802553689128974
--
1508895895168995334
1508890501210161159
--
1508895851447468033
1508857887572983811
--
1508895800126066695
1508890501210161159
--
1508895786377134088
1508884492324425729
--
1508895765808226304
1508643632039043073
--
1508895752751251458
1508827809040326658
--
1508895752403124224
1508802378685992961
--
1508895750968668161
1508889266327220225
--
1508895724179800068
1508646694782652420
--
1508895716520857602
1508793851007414272
--
1508895710506192899
1508895376497016832
--
1508895689979404303
1508643632039043073
--
1508895672531132428
1508894309751398414
--
1508895668714106883
1508868814313713664
--
1508895666461892608
1508800151640584193
--
1508895648900259841
1508889266327220225
--
1508895631665889281
1508895630776680448
--
1508895591916441601
1508838092827860996
--
1508895586677886977
1508891733656018955
--
1508895586384289794
1507695921374670850
--
1508895584408670210
--
1508895581002944514
1508894285332029445
--
15088955

--
1508878412752031753
--
1508878402803183616
1508806091664150535
--
1508878378450907136
1508868814313713664
--
1508878369567424514
1508851479561621511
--
1508878359559868432
1508858575833157639
--
1508878303586779136
1508581225790947328
--
1508878290576023556
1508475260529778698
--
1508878247383248898
1508878245713768458
--
1508878238294097922
1508878236490547201
--
1508878207679823872
--
1508878194035752961
1508643632039043073
--
1508878179380908041
1508387066228396036
--
1508878126700544000
1508877955757445126
--
1508878105712070657
--
1508878091669557251
1508845335178891266
--
1508878002440048645
1508643632039043073
--
1508878001156591628
1508874236122877956
--
1508877984907743232
1508643632039043073
--
1508877969254752256
1508826532600496130
--
1508877955757445126
--
1508877924987985932
1508866187232526336
--
1508877902695346176
--
1508877887910383625
1508876085706039300
--
1508877879765090304
1508643632039043073
--
1508877878569705472
1508643632039043073
--
1508877849830182915
15

--
1508860911779524613
1508678596730183682
--
1508860873938386946
1508855630571970565
--
1508860871614754817
1508568186358165505
--
1508860860671873028
1508643632039043073
--
1508860828862267393
1508851709438840836
--
1508860812445716481
1508850772473225223
--
1508860803537158148
1508800151640584193
--
1508860759421423620
--
1508860747899551744
1507787803014410243
--
1508860747652206595
1508571459333074945
--
1508860703129718789
1508814215930421249
--
1508860658074648578
1508829797723480064
--
1508860651594203139
1508819166798954497
--
1508860647202701312
--
1508860606933176321
1508643632039043073
--
1508860605163347979
1508643632039043073
--
1508860593251442691
1508643632039043073
--
1508860576335900677
1507308749303734284
--
1508860553862778884
1508646694782652420
--
1508860528340439047
1508838296528564233
--
1508860483104874501
1508643632039043073
--
1508860421771436035
1508812425855913999
--
1508860417451479042
1508855630571970565
--
1508860400569356295
1508553914974715910
--
15088

...

--
1505929806713700356
--
1505929806340411398
--
1505929804645863431
--
1505929756860039171
--
1505929727084621828
--
1505929676023230466
--
1505929567227179011
--
1505929546956222466
--
1505929472771506177
--
1505929401292267532
--
1505929366613680135
--
1505929356052516870
--
1505929340382498818
--
1505929311856988163
--
1505929220676984836
--
1505929195368591361
--
1505929190201303041
--
1505929174728515589
--
1505929044608622592
--
1505928964736434179
--
1505928900379131909
--
1505928809073328128
--
1505928755826601985
--
1505928675048538121
--
1505928647894618118
--
1505928643096334342
--
1505928548330127361
--
1505928429849436167
--
1505928371703799814
--
1505928339147698181
--
1505928333334392840
--
1505928219458867206
--
1505928190111502342
--
1505928182733627398
--
1505928153260339202
--
1505927963812012042
--
1505927936297340942
--
1505927919721492482
--
1505927912704385029
--
1505927858623029248
--
1505927821159452674
--
1505927778365026313
--
1505927707590377476
--
15059276

1505844482410881026
--
1505844431299444736
--
1505844311795113986
--
1505844309991505924
--
1505844138775916544
--
1505844047784538115
--
1505844042927587331
--
1505843999025688579
--
1505843990603747331
--
1505843916129636357
--
1505843914590281730
--
1505843881136508932
--
1505843808172494851
--
1505843785116360709
--
1505843697803755520
--
1505843628836474880
--
1505843615955927040
--
1505843470749085696
--
1505843351005937665
--
1505843143358525443
--
1505843131631161346
--
1505843113625018373
--
1505843038618324996
--
1505842955994767360
--
1505842844367572998
--
1505842754571677696
--
1505842644236210180
--
1505842229822332929
--
1505842079330713602
--
1505842078130921473
--
1505842002654633985
--
1505841779031031809
--
1505841645807362052
--
1505841618489942020
--
1505841592996925440
--
1505841545810952194
--
1505841525686685696
--
1505841372418363398
--
1505841264805167104
--
1505841183108575235
--
1505841152901136384
--
1505841143573004288
--
1505841045497602048
--
15058409927

1505700188622577665
--
1505700150257205250
--
1505700121828556810
--
1505700108205461510
--
1505700065939271680
--
1505700051296964616
--
1505700025397125121
--
1505699885856735232
--
1505699777371152396
--
1505699590980481029
--
1505699495811633152
--
1505699277095391232
--
1505699253963788289
--
1505699190629937152
--
1505699151761321987
--
1505699144270290945
--
1505698972966731777
--
1505698948509736963
--
1505698889361416197
--
1505698783618863104
--
1505698741034315776
--
1505698714790281220
--
1505698462624776194
--
1505698381108510720
--
1505698185456541707
--
1505698035338256397
--
1505698006108196865
--
1505698005433069568
--
1505697801078206465
--
1505697731729408000
--
1505697711672430594
--
1505697584987340803
--
1505697566021009409
--
1505697511641686019
--
1505697449025085440
--
1505697424756690944
--
1505697322604417026
--
1505697278111084546
--
1505697179545001988
--
1505697131654311940
--
1505697122691260427
--
1505697099870052360
--
1505696970870247425
--
15056969512

--
1505615928423297031
--
1505615897662091265
--
1505615895774826499
--
1505615878406160387
--
1505615874761412608
--
1505615865886253059
--
1505615749724975113
--
1505615735778914306
--
1505615731966169088
--
1505615710420152321
--
1505615690211995649
--
1505615678941777921
--
1505615659786506245
--
1505615645118918656
--
1505615639527972868
--
1505615539170942984
--
1505615455247118344
--
1505615437941571584
--
1505615413249560578
--
1505615368768962578
--
1505615351136100359
--
1505615156591616004
--
1505614830249472002
--
1505614817809289218
--
1505614763048513544
--
1505614625529860099
--
1505614485783990279
--
1505614456709009409
--
1505614423221809172
--
1505614380737921024
--
1505614378107736064
--
1505614315860099072
--
1505614315390439427
--
1505614300714790913
--
1505614264458874883
--
1505614192296009743
--
1505614080999976960
--
1505614048200695810
--
1505613997382451209
--
1505613990726189059
--
1505613961286209541
--
1505613878188666881
--
1505613872580939783
--
15056138

--
1505533612187344905
--
1505533550057213961
--
1505533377302122496
--
1505533364706570243
--
1505533349263204354
--
1505533277813325832
--
1505533244577619970
--
1505533186285133833
--
1505533134653120513
--
1505533051639676930
--
1505532993384951808
--
1505532977144496128
--
1505532956135276546
--
1505532855153213441
--
1505532811083722753
--
1505532723351498753
--
1505532672692535300
--
1505532610373734406
--
1505532601087451138
--
1505532583039447047
--
1505532539611631625
--
1505532349357989888
--
1505532287861014535
--
1505532182529462286
--
1505532138506100739
--
1505532123368894467
--
1505532109275938826
--
1505532106172248070
--
1505532085695512576
--
1505531973502214145
--
1505531926723153922
--
1505531912823136261
--
1505531853712896003
--
1505531804631064578
--
1505531540088008708
--
1505531520882253824
--
1505531397041238020
--
1505531276920512514
--
1505531270813696004
--
1505531254434775043
--
1505531221987713025
--
1505531212064079879
--
1505531207215468545
--
15055311

In [52]:
# printing out the number of nodes (users) in our graph
print (len(G2.nodes()))
# printing out the number of edges/links in our graph
print (len(G2.edges()))

43906
27095


In [53]:
# writing our graph to a Gephi file format
nx.write_gexf(G2, "homelessness_retweets.gexf")

In [54]:
#get the huge nodes

sorted(G2.degree, key=lambda x: x[1], reverse=True)


#########################################
#############     TOP3     ##############
#########################################
#('1511449706433548292', 6229)
#('1508643632039043073', 913),
#('1514612289516625924', 864),

#('1514567970047107072', 493),
#('1514604762435530759', 415),
#('1513777971919613952', 394),
#('1508646694782652420', 348)

[('1511449706433548292', 6229),
 ('1508643632039043073', 913),
 ('1514612289516625924', 864),
 ('1514567970047107072', 493),
 ('1514604762435530759', 415),
 ('1513777971919613952', 394),
 ('1508646694782652420', 348),
 ('1514517267257700354', 322),
 ('1514616448081018886', 318),
 ('1508761410922516480', 296),
 ('1514604137123516432', 292),
 ('1508890501210161159', 284),
 ('1508581225790947328', 241),
 ('1514617155706187778', 237),
 ('1511846982414962699', 198),
 ('1508623750903709697', 185),
 ('1514599614246137859', 180),
 ('1511904409449648137', 178),
 ('1508553914974715910', 171),
 ('1508838044346064902', 167),
 ('1508681591379607555', 143),
 ('1508822596921479178', 137),
 ('1514345945567178754', 133),
 ('1508829797723480064', 131),
 ('1508727710042173440', 124),
 ('1514442354811416581', 87),
 ('1508739410367377409', 86),
 ('1514580098002964480', 85),
 ('1511759836798726156', 82),
 ('1514633160511967235', 82),
 ('1514590243441332234', 77),
 ('1508571459333074945', 74),
 ('15088661872

In [55]:
info = {"api_key": "EA0Nc1ZdovL6026feB6QzC42a",
        "api_key_secret": "bbnyEELzI06L3pNCfHdLeOkTio5L6kT5KKH4eKRUXwfNrG4JQ",
        "bearer_token" : "AAAAAAAAAAAAAAAAAAAAAA2hYgEAAAAA8OUr3Ab8wV2SBd7AQz3UxblZ%2FFM%3Dl5bbd1hC9D6tsWDN1HNtqm1SHC4Dgy56ZrjwPr4FlJWWFE8E3K",
        "access_token": "1487509017362513921-lZvWsFfvOFrSyO1pRwMJ1nIxpuA2oi",
        "access_token_secret": "wm7cetupMABoics4sHxrzKeC9TpDEB4mGVRMEEkqDZr72"}

client = tweepy.Client(
    consumer_key       = info["api_key"],
    consumer_secret    = info["api_key_secret"],
    bearer_token       = info["bearer_token"],
    access_token       = info["access_token"],
    access_token_secret= info["access_token_secret"],
    wait_on_rate_limit = True
)

In [56]:
#Analysing the TOP3 tweets
TOP1tweet = client.get_tweet(1511449706433548292)
print(TOP1tweet)
#https://twitter.com/joeywreck/status/1511449706433548292

TOP2tweet = client.get_tweet(1508643632039043073)
print(TOP2tweet)
#https://twitter.com/JoshuaPotash/status/1508643632039043073

TOP3tweet = client.get_tweet(1514612289516625924)
print(TOP3tweet)
#https://twitter.com/hasanthehun/status/1514612289516625924

Response(data=<Tweet id=1511449706433548292 text='A reminder that a man with enough money to end homelessness in America decided to buy a 9% stake in Twitter instead.'>, includes={}, errors=[], meta={})
Response(data=<Tweet id=1508643632039043073 text="Once again, I don't understand people who think homelessness is a problem for cops to solve, not a problem for a house to solve.">, includes={}, errors=[], meta={})
Response(data=<Tweet id=1514612289516625924 text='this mf said hitler overcame homelessness so you can too. tennessee is something else.  https://t.co/E1QmOlY7Zz'>, includes={}, errors=[], meta={})
